#Paquetes necesarios

In [2]:
import cv2  
import math 

from ultralytics import YOLO

Entrenamiento del modelo para detectar matrículas

In [ ]:
model = YOLO("yolo11n.pt")

results = model.train(data="datasets/data.yaml", epochs=20, imgsz=640)

Uso del modelo para la detección.

In [3]:
model = YOLO("yolo11n.pt")
filename = "C0142.MP4"

#results = model.track(source=filename, show=True)  # BoT-SORT tracker (por defecto)
results = model.track(source=filename, show=True, tracker="bytetrack.yaml")  # ByteTrack tracker

cv2.destroyAllWindows()



WARNING  inference results will accumulate in RAM unless `stream=True` is passed, causing potential out-of-memory
errors for large sources or long-running streams and videos. See https://docs.ultralytics.com/modes/predict/ for help.

Example:
    results = model(source=..., stream=True)  # generator of Results objects
    for r in results:
        boxes = r.boxes  # Boxes object for bbox outputs
        masks = r.masks  # Masks object for segment masks outputs
        probs = r.probs  # Class probabilities for classification outputs

video 1/1 (frame 1/2832) c:\Users\Sara\VisualStudioProjects\P4\C0142.MP4: 384x640 1 car, 1 bus, 335.0ms
video 1/1 (frame 2/2832) c:\Users\Sara\VisualStudioProjects\P4\C0142.MP4: 384x640 1 car, 1 bus, 155.0ms
video 1/1 (frame 3/2832) c:\Users\Sara\VisualStudioProjects\P4\C0142.MP4: 384x640 1 car, 1 bus, 139.0ms
video 1/1 (frame 4/2832) c:\Users\Sara\VisualStudioProjects\P4\C0142.MP4: 384x640 1 car, 1 bus, 153.0ms
video 1/1 (frame 5/2832) c:\Users\Sara\Vis

In [3]:
import cv2  
import math 
import csv
import numpy as np
from ultralytics import YOLO
import pytesseract

# Configuración de Tesseract para OCR
pytesseract.pytesseract.tesseract_cmd = r'C:/Program Files/Tesseract-OCR/tesseract'

# Cargar modelos
model_deteccion = YOLO("yolo11n.pt")  # Modelo YOLO para detectar personas y vehículos
model_matriculas = YOLO("runs/detect/train3/weights/best.pt")  # Modelo para detectar matrículas

# Nombre del archivo de video
filename = "C0142.MP4"

# Abrir archivo CSV para guardar los resultados
csv_file = open('detecciones.csv', mode='w', newline='')
csv_writer = csv.writer(csv_file)
csv_writer.writerow(['fotograma', 'tipo_objeto', 'confianza', 'identificador_tracking', 'x1', 'y1', 'x2', 'y2', 'matrícula_en_su_caso', 'confianza_matricula', 'mx1', 'my1', 'mx2', 'my2', 'texto_matricula'])

# Abrir el video
cap = cv2.VideoCapture(filename)

frame_count = 0
while True:
    ret, frame = cap.read()
    if not ret:
        break

    # Detección de vehículos y personas
    results = model_deteccion(frame, stream=True)

    for r in results:
        boxes = r.boxes

        for box in boxes:
            # Extraer coordenadas de la caja delimitadora
            x1, y1, x2, y2 = box.xyxy[0]
            x1, y1, x2, y2 = int(x1), int(y1), int(x2), int(y2)

            # Clase y confianza de la detección
            cls = int(box.cls[0])
            confianza = math.ceil((box.conf[0] * 100)) / 100
            tipo_objeto = model_deteccion.names[cls]  # Obtener la etiqueta de clase

            # Si es un vehículo, intentamos detectar la matrícula
            matricula_text = ""
            conf_matricula = 0
            mx1, my1, mx2, my2 = 0, 0, 0, 0
            if tipo_objeto in ["car", "truck", "bus", "motorbike"]:
                # Usar modelo de OCR para detectar matrícula en la región de interés (ROI)
                vehiculo_roi = frame[y1:y2, x1:x2]  # Recortar la imagen solo en el área del vehículo
                matricula_results = model_matriculas(vehiculo_roi, stream=True)
                
                # Si hay detecciones de matrículas, procesarlas
                for mat_result in matricula_results:
                    mat_boxes = mat_result.boxes
                    for mat_box in mat_boxes:
                        mx1, my1, mx2, my2 = mat_box.xyxy[0]
                        mx1, my1, mx2, my2 = int(mx1), int(my1), int(mx2), int(my2)
                        
                        # Convertir a imagen y usar OCR para texto
                        matricula_roi = vehiculo_roi[my1:my2, mx1:mx2]
                        if matricula_roi is not None:
                            matricula_text = pytesseract.image_to_string(matricula_roi, config='--psm 7')
                            conf_matricula = math.ceil((mat_box.conf[0] * 100)) / 100
                        else:
                            matricula_text = ""
                            conf_matricula = 0
            
            # Guardar resultados en el CSV
            csv_writer.writerow([frame_count, tipo_objeto, confianza, box.id[0] if box.id else '', x1, y1, x2, y2, matricula_text, conf_matricula, mx1, my1, mx2, my2, matricula_text])
            
            # Dibujar en la imagen
            cv2.rectangle(frame, (x1, y1), (x2, y2), (255, 0, 0), 2)  # Dibuja rectángulo
            cv2.putText(frame, f"{tipo_objeto} {confianza}", (x1, y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (255, 0, 0), 2)
            if matricula_text:
                cv2.putText(frame, f"Matrícula: {matricula_text}", (x1, y2 + 20), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (0, 255, 0), 2)

    # Mostrar el video con las detecciones
    cv2.imshow('Detección y Seguimiento', frame)

    frame_count += 1
    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

# Cerrar todo
cap.release()
csv_file.close()
cv2.destroyAllWindows()



0: 384x640 4 cars, 1 bus, 347.4ms

0: 544x640 (no detections), 225.9ms
Speed: 9.8ms preprocess, 225.9ms inference, 2.0ms postprocess per image at shape (1, 3, 544, 640)

0: 512x640 (no detections), 242.2ms
Speed: 8.7ms preprocess, 242.2ms inference, 1.6ms postprocess per image at shape (1, 3, 512, 640)

0: 416x640 (no detections), 235.2ms
Speed: 7.1ms preprocess, 235.2ms inference, 1.0ms postprocess per image at shape (1, 3, 416, 640)

0: 416x640 (no detections), 165.6ms
Speed: 5.9ms preprocess, 165.6ms inference, 1.0ms postprocess per image at shape (1, 3, 416, 640)

0: 480x640 (no detections), 197.1ms
Speed: 4.9ms preprocess, 197.1ms inference, 1.0ms postprocess per image at shape (1, 3, 480, 640)
Speed: 17.6ms preprocess, 347.4ms inference, 20.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 cars, 1 bus, 207.4ms

0: 512x640 (no detections), 175.0ms
Speed: 8.8ms preprocess, 175.0ms inference, 1.0ms postprocess per image at shape (1, 3, 512, 640)

0: 512x640 (no dete